# Get Taco Bell locations

#### Load Python tools and Jupyter config

In [1]:
import us
import json
import black
import requests
import us as usa
import pandas as pd
import jupyter_black
import altair as alt
import geopandas as gpd
import datetime as datetime
from bs4 import BeautifulSoup
from vega_datasets import data
from tqdm.notebook import tqdm, trange
from json.decoder import JSONDecodeError

In [2]:
jupyter_black.load()
pd.options.display.max_columns = 100
pd.options.display.max_rows = 1000
pd.options.display.max_colwidth = None
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [3]:
current_time = datetime.datetime.now()
epoch_time_milliseconds = int(current_time.timestamp() * 1000)

In [4]:
place = "taco-bell"
place_formal = "Taco Bell"
color = "#A77BCA"

## ZIP Codes

#### Read a list, sorted by population

In [5]:
zips = (
    gpd.read_file("../../_reference/data/zips_centroids.geojson")[
        ["ID", "NAME", "STATE_NAME", "ST_ABBREV", "TOTPOP_CY", "geometry"]
    ]
    .sort_values("TOTPOP_CY", ascending=False)
    .rename(columns={"TOTPOP_CY": "pop", "ST_ABBREV": "state_abbr"})
    .reset_index(drop=True)
)

In [6]:
zips.columns = zips.columns.str.lower()

#### Let's get locations for 4,000 zips: The most-populous 1,000, and then 2,000 as a sample from the rest

In [7]:
length = len(zips) - 2000
large = zips.head(2000)
sample = zips.tail(length).sample(2000)

In [8]:
zips_concat = pd.concat([large, sample])
zips_concat["latitude"] = zips_concat.geometry.y
zips_concat["longitude"] = zips_concat.geometry.x

In [9]:
zips_concat.dtypes

id              object
name            object
state_name      object
state_abbr      object
pop              int64
geometry      geometry
latitude       float64
longitude      float64
dtype: object

In [10]:
response_list = []

for k, v in tqdm(zips_concat.iterrows(), total=len(zips_concat)):

    latitude = v["latitude"]
    longitude = v["longitude"]

    headers = {
        "authority": "www.tacobell.com",
        "accept": "*/*",
        "accept-language": "en-US,en;q=0.9,es;q=0.8",
        "referer": "https://www.tacobell.com/locations",
        "sec-ch-ua": '"Not A(Brand";v="99", "Google Chrome";v="121", "Chromium";v="121"',
        "sec-ch-ua-mobile": "?0",
        "sec-ch-ua-platform": '"macOS"',
        "sec-fetch-dest": "empty",
        "sec-fetch-mode": "cors",
        "sec-fetch-site": "same-origin",
        "user-agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/121.0.0.0 Safari/537.36",
        "x-datadog-origin": "rum",
        "x-datadog-parent-id": "4244205488407588760",
        "x-datadog-sampled": "1",
        "x-datadog-sampling-priority": "1",
        "x-datadog-trace-id": "8520671479567972177",
    }

    params = {
        "latitude": f"{latitude}",
        "longitude": f"{longitude}",
        "_": epoch_time_milliseconds,
    }

    response = requests.get(
        "https://www.tacobell.com/tacobellwebservices/v4/tacobell/stores",
        params=params,
        headers=headers,
    )

    try:
        # Try to decode JSON response
        near_by_stores = response.json().get("nearByStores", [])
    except JSONDecodeError as e:
        # If there's an error decoding JSON, print an error message and continue to the next location
        print(
            f"Error decoding JSON response for latitude {latitude} and longitude {longitude}: {e}"
        )
        continue

    if not near_by_stores:
        print(
            f"No nearby stores found for latitude {latitude} and longitude {longitude}. Skipping..."
        )
        continue

    response_list.append(response)

  0%|          | 0/4000 [00:00<?, ?it/s]

Error decoding JSON response for latitude 43.56007403124513 and longitude -114.29469236976817: Expecting value: line 1 column 1 (char 0)
No nearby stores found for latitude nan and longitude nan. Skipping...
Error decoding JSON response for latitude 44.40116714173707 and longitude -98.2048432859499: Expecting value: line 1 column 1 (char 0)
No nearby stores found for latitude 40.64902002222819 and longitude -107.75204893200934. Skipping...
Error decoding JSON response for latitude 46.61035458402066 and longitude -90.81383277781002: Expecting value: line 1 column 1 (char 0)
Error decoding JSON response for latitude 48.25531056843622 and longitude -103.74253824645626: Expecting value: line 1 column 1 (char 0)
No nearby stores found for latitude 58.46403418142095 and longitude -134.17859320930677. Skipping...
Error decoding JSON response for latitude 38.28698370342466 and longitude -109.60837185517515: Expecting value: line 1 column 1 (char 0)
Error decoding JSON response for latitude 59.

In [11]:
dict_list = []

for r in response_list:
    zip_response = r.json()["nearByStores"]
    for z in zip_response:
        location_dict = {
            "store_num": z["storeNumber"],
            "timezone": z["timeZoneCity"],
            "address": z["address"]["line1"],
            "city": z["address"]["town"],
            "state": z["address"]["region"],
            "zip": z["address"]["postalCode"],
            "phone": z["phoneNumber"],
            "latitude": z["geoPoint"]["latitude"],
            "longitude": z["geoPoint"]["longitude"],
        }
        dict_list.append(location_dict)

In [12]:
df = pd.DataFrame(dict_list).drop_duplicates(subset="store_num").reset_index()

In [13]:
len(df)

7148

#### State codes

In [14]:
df["state_abbr"] = pd.json_normalize(df["state"])
df["state_abbr"] = df["state_abbr"].str.replace("US-", "")

#### Create a mapping of state abbreviations to full state names using the us library

In [15]:
state_mapping = {state.abbr: state.name for state in usa.states.STATES}

#### New column of full state names based on abbreviations

In [16]:
df["state_name"] = df["state_abbr"].map(state_mapping)

In [17]:
df.head()

index store_num         timezone                   address      city  \
0      0    027800  America/Chicago  25109 Market Place Drive      Katy   
1      1    024393  America/Chicago    23557 Westheimer Pkwy.      Katy   
2      2    030623  America/Chicago             26628 FM 1093  Richmond   
3      3    026789  America/Chicago    5640 W Grand Parkway S  Richmond   
4      4    003566  America/Chicago            601 S Mason Rd      Katy   

                  state    zip         phone   latitude  longitude state_abbr  \
0  {'isocode': 'US-TX'}  77494  +12818459250  29.781831 -95.803263         TX   
1  {'isocode': 'US-TX'}  77494  +12813913504  29.733199 -95.775279         TX   
2  {'isocode': 'US-TX'}  77406  +13467624346  29.696201 -95.838742         TX   
3  {'isocode': 'US-TX'}  77406  +12812325738  29.691420 -95.771584         TX   
4  {'isocode': 'US-TX'}  77450  +12815781342  29.774475 -95.751225         TX   

  state_name  
0      Texas  
1      Texas  
2      Texas  
3      Texas  
4      Texas

---

## Geography

#### Make it a geodataframe

In [18]:
df_geo = df.copy()

In [19]:
gdf = gpd.GeoDataFrame(
    df_geo, geometry=gpd.points_from_xy(df_geo.longitude, df_geo.latitude)
)

In [20]:
locations_gdf = gdf.set_crs("EPSG:4326").copy()

---

## Maps

#### US states background

In [21]:
background = (
    alt.Chart(alt.topo_feature(data.us_10m.url, feature="states"))
    .mark_geoshape(fill="#e9e9e9", stroke="white")
    .properties(width=800, height=500, title=f"{place_formal} locations")
    .project("albersUsa")
)

#### Location points map

In [22]:
points = (
    alt.Chart(gdf)
    .mark_circle(size=5, color=color)
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
    )
)

point_map = background + points
point_map.configure_view(stroke=None)

alt.LayerChart(...)

#### Location proportional symbols map

In [23]:
symbols = (
    alt.Chart(gdf)
    .transform_aggregate(
        latitude="mean(latitude)",
        longitude="mean(longitude)",
        count="count()",
        groupby=["state_name"],
    )
    .mark_circle()
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
        size=alt.Size("count:Q", title="Count by state"),
        color=alt.value(color),
        tooltip=["state_name:N", "count:Q"],
    )
    .properties(
        title=f"Number of {place_formal} in US, by average lon/lat of locations"
    )
)

symbol_map = background + symbols
symbol_map.configure_view(stroke=None)

alt.LayerChart(...)

---

## Exports

#### JSON

In [24]:
df.to_json(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.json",
    indent=4,
    orient="records",
)

#### CSV

In [25]:
df.to_csv(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.csv", index=False
)

#### GeoJSON

In [26]:
locations_gdf.to_file(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.geojson",
    driver="GeoJSON",
)